In [1]:
# Run if working locally
%load_ext autoreload
%autoreload 2
%load_ext nb_black

<IPython.core.display.Javascript object>

In [2]:
import sqlite3
from sqlite3 import Error
import pickle
import os, sys
import config

config.root_path = os.path.abspath(os.path.join(os.getcwd(), ".."))
sys.path.insert(0, config.root_path)

from db.dbv2 import Table, AugmentedTable, TrainTestTable

<IPython.core.display.Javascript object>

In [3]:
from src.dataset.gpt_augmentor import Augmentor

2023-01-02 20:08:39.914918: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:306] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2023-01-02 20:08:39.915502: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:272] Created TensorFlow device (/job:localhost/replica:0/task:0/device:GPU:0 with 0 MB memory) -> physical PluggableDevice (device: 0, name: METAL, pci bus id: <undefined>)


Metal device set to: Apple M1 Max


All model checkpoint layers were used when initializing TFGPT2LMHeadModel.

All the layers of TFGPT2LMHeadModel were initialized from the model checkpoint at gpt2.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFGPT2LMHeadModel for predictions without further training.


<IPython.core.display.Javascript object>

In [36]:
import numpy as np
import nltk
from nltk.tokenize import word_tokenize
from src.dataset.utils import (
    truncate_by_char,
    truncate_by_sentence,
    avg_segment_length_by_char,
)

<IPython.core.display.Javascript object>

In [34]:
truncate_by_char("this is a sentence. and another . and one more .", 5)
truncate_by_sentence("this is a sentence. and another . and one more .", 2)

'this is a sentence. and another .'

<IPython.core.display.Javascript object>

In [35]:
avg_segment_length_by_char(["one string", "two string", "three"])

8.0

<IPython.core.display.Javascript object>

In [9]:
dataset_type = "committee"

table = Table(dataset_type)

target_sentences_original = table.get_target_sentences()

segments = []

for target in target_sentences_original:
    segment = table.get_segment(target[0])
    segments.append([x[1] for x in segment])



[["thank you very much for that question , chair . i 've got to say 'yes ' , in many regards . so , the key focus of the programme in the early stages was about improving access to specialist child and adolescent mental health services . we developed the windscreen model—or we lifted the windscreen model . other models that are very similar have been talked about as well , and our big focus was on ensuring that we could make immediate progress around access to specialist camhs . it 's some years ago now since this committee did the original report , and obviously healthcare inspectorate wales and the wales audit office had done reports in the past , and i think there was a need for a programme that could focus on action . you 'll see in the written update that we covered quite a large number of areas , and so therefore had to make a prioritisation . the prioritisation was at the specialist camhs end . we have provided the committee with a red , amber or green rating of where we feel th

<IPython.core.display.Javascript object>

## Batch Upload

In [ ]:
dataset_type = "committee"

table = Table(dataset_type)
augmented_table = AugmentedTable(dataset_type)
train_test_table = TrainTestTable(dataset_type)

min_sent_tokens = 8
max_sent_tokens = 64

target_sentences_original = table.get_target_sentences()
target_sentences = [s[1] for s in target_sentences_original]
cleaned_target_sentences = []

for s in target_sentences:
    if len(word_tokenize(s)) > min_sent_tokens:
        shortened_sentence = " ".join(word_tokenize(s)[:max_sent_tokens])
        cleaned_target_sentences.append(shortened_sentence)

augmented_segments = Augmentor.augment_gpt2(
    cleaned_target_sentences[:2],
    fast=True,
    # multiply by 5 to account for 5 as a max segment
    max_seq_word_length=max_sent_tokens * 5,
    verbose=True,
)